(content:post_process_collection)=
# Post-processing the CSV file created by pySocialWatcher

So far, we have: 
1. [Created a development account and generated a token for our collection](getting_your_token)
2. [Learned how to run a data collection](content:basic_example)
3. [Learned how to customize our collection and save the results to disk](content:json_creation)

We now assume that a file named ``output_psw_top5_cities.csv`` is created on disk after processing the [previous notebook](content:json_creation).

Now we will learn how to use pySocialWatcher tools to post-process the data collected and create a human-readable file, which is also ready [to plot some maps](content:plotting_maps).

In [11]:
import pandas as pd
from pysocialwatcher import post_process

In [12]:
df = pd.read_csv("./output_psw_top5_cities.csv")
df.head(5)

Unnamed: 0  name  interests  ages_ranges  genders  behavior  scholarities  \
0           0  test        NaN  {'min': 18}        0       NaN           NaN   
1           1  test        NaN  {'min': 18}        0       NaN           NaN   
2           2  test        NaN  {'min': 18}        0       NaN           NaN   
3           3  test        NaN  {'min': 18}        0       NaN           NaN   
4           4  test        NaN  {'min': 18}        0       NaN           NaN   

   languages  family_statuses  relationship_statuses  ...  \
0        NaN              NaN                    NaN  ...   
1        NaN              NaN                    NaN  ...   
2        NaN              NaN                    NaN  ...   
3        NaN              NaN                    NaN  ...   
4        NaN              NaN                    NaN  ...   

  household_composition                                         all_fields  \
0                   NaN  (('ages_ranges', {'min': 18}), ('genders', 0),...   
1                   NaN  (('ages_ranges', {'min': 18}), ('genders', 0),...   
2                   NaN  (('ages_ranges', {'min': 18}), ('genders', 0),...   
3                   NaN  (('ages_ranges', {'min': 18}), ('genders', 0),...   
4                   NaN  (('ages_ranges', {'min': 18}), ('genders', 0),...   

                                           targeting  \
0  {'geo_locations': {'cities': [{'key': 2880782,...   
1  {'geo_locations': {'cities': [{'key': 2490299,...   
2  {'geo_locations': {'cities': [{'key': 2673660,...   
3  {'geo_locations': {'cities': [{'key': 1035921,...   
4  {'geo_locations': {'cities': [{'key': 269969, ...   

                                            response dau_audience  \
0  b'{"data":[{"daily_outcomes_curve":[{"spend":0...            0   
1  b'{"data":[{"daily_outcomes_curve":[{"spend":0...            0   
2  b'{"data":[{"daily_outcomes_curve":[{"spend":0...          463   
3  b'{"data":[{"daily_outcomes_curve":[{"spend":0...         5055   
4  b'{"data":[{"daily_outcomes_curve":[{"spend":0...          777   

   mau_audience                          access_device   timestamp  \
0          1000  {'name': '2G', 'or': [6017253486583]}  1614166082   
1          1000  {'name': '2G', 'or': [6017253486583]}  1614166082   
2          1700  {'name': '2G', 'or': [6017253486583]}  1614166082   
3         14000  {'name': '2G', 'or': [6017253486583]}  1614166082   
4          2000  {'name': '2G', 'or': [6017253486583]}  1614166082   

   publisher_platforms mock_response  
0         ["facebook"]         False  
1         ["facebook"]         False  
2         ["facebook"]         False  
3         ["facebook"]         False  
4         ["facebook"]         False  

[5 rows x 21 columns]

There are two main functions from `pySocialWatcher` to post-process the collection and they need to be used in the following order:
1. ``post_process.post_process_df_collection`` creates new columns based on what was used in the collection. For example, there will be a new column for Gender, Ages, Education, Device, etc.
2. ``post_process.combine_cols`` generates, given a (sub)set of columns created by ``post_process.post_process_df_collection``, a new dataframe that combines the columns and has as many rows as unique locations in the collection.

In [13]:
processed_df = post_process.post_process_df_collection(df)
processed_df.head(4)[["LocationType", "FullLocation", "Gender", "Ages", "Education"]]

LocationType                       FullLocation Gender Ages   Education
0         city               Minato-ku, Tokyo, JP   both  18-  AllDegrees
1         city             New York, New York, US   both  18-  AllDegrees
2         city  Mexico City, Distrito Federal, MX   both  18-  AllDegrees
3         city            Mumbai, Maharashtra, IN   both  18-  AllDegrees

In [16]:
# We then combine the columns to obtain a dataframe in which every single line is the data for a location
cols_to_combine = ["Gender", "Ages", "Device"]
combo_df = post_process.combine_cols(processed_df, cols_to_combine)

combo_df = combo_df.pivot(index="Key", columns="combo", values="mau_audience").reset_index()
combo_df.head()

combo      Key  both_18-40_2G  both_18-40_3G  both_18-40_4G  \
0       269969           1000          45000         510000   
1      1035921          11000          46000        5300000   
2      2490299           1000           4900         520000   
3      2673660           1200         160000        1000000   
4      2880782           1000           1000           8400   

combo  both_18-40_AllDevices  both_18-40_Wifi  both_18-_2G  both_18-_3G  \
0                    5800000          3700000         2000        88000   
1                    9000000          1700000        14000        58000   
2                    3300000          1600000         1000        11000   
3                    7600000          4800000         1700       240000   
4                      64000            34000         1000         1000   

combo  both_18-_4G  both_18-_AllDevices  ...  male_41-54_2G  male_41-54_3G  \
0           870000              9800000  ...           1000          12000   
1          6500000             11000000  ...           1800           5700   
2          1100000              5900000  ...           1000           1700   
3          1400000             11000000  ...           1000          28000   
4            15000               120000  ...           1000           1000   

combo  male_41-54_4G  male_41-54_AllDevices  male_41-54_Wifi  male_55-_2G  \
0             120000                1000000           610000         1000   
1             640000                1100000           290000         1000   
2             150000                 670000           300000         1000   
3             180000                1100000           710000         1000   
4               2900                  23000            12000         1000   

combo  male_55-_3G  male_55-_4G  male_55-_AllDevices  male_55-_Wifi  
0             9300        68000               600000         370000  
1             2700       210000               450000         170000  
2             2000       130000               540000         270000  
3            17000        77000               590000         410000  
4             1000         1500                11000           5600  

[5 rows x 61 columns]

An important trick is to recover what are the locations that each Key refers to.
For that, we can use the ``processed_df`` dataframe again as follows:

In [17]:
# Get the unique set of <Key, location>
location_mapping = processed_df[["Key", "Name", "Region", "FullLocation"]].drop_duplicates()

# Merge it back to the post-processed dataframe
final_df = pd.merge(location_mapping, combo_df)
final_df

Key         Name             Region                       FullLocation  \
0  2880782    Minato-ku              Tokyo               Minato-ku, Tokyo, JP   
1  2490299     New York           New York             New York, New York, US   
2  2673660  Mexico City   Distrito Federal  Mexico City, Distrito Federal, MX   
3  1035921       Mumbai        Maharashtra            Mumbai, Maharashtra, IN   
4   269969    São Paulo  São Paulo (state)   São Paulo, São Paulo (state), BR   

   both_18-40_2G  both_18-40_3G  both_18-40_4G  both_18-40_AllDevices  \
0           1000           1000           8400                  64000   
1           1000           4900         520000                3300000   
2           1200         160000        1000000                7600000   
3          11000          46000        5300000                9000000   
4           1000          45000         510000                5800000   

   both_18-40_Wifi  both_18-_2G  ...  male_41-54_2G  male_41-54_3G  \
0            34000         1000  ...           1000           1000   
1          1600000         1000  ...           1000           1700   
2          4800000         1700  ...           1000          28000   
3          1700000        14000  ...           1800           5700   
4          3700000         2000  ...           1000          12000   

   male_41-54_4G  male_41-54_AllDevices  male_41-54_Wifi  male_55-_2G  \
0           2900                  23000            12000         1000   
1         150000                 670000           300000         1000   
2         180000                1100000           710000         1000   
3         640000                1100000           290000         1000   
4         120000                1000000           610000         1000   

   male_55-_3G  male_55-_4G  male_55-_AllDevices  male_55-_Wifi  
0         1000         1500                11000           5600  
1         2000       130000               540000         270000  
2        17000        77000               590000         410000  
3         2700       210000               450000         170000  
4         9300        68000               600000         370000  

[5 rows x 64 columns]

And we are done! 
Look how we combined, respectively, the dimensions <Gender, Age, Device> to generate columns like __"both_18-40_2G"__ meaning _both_ male and female FB audience aged _18 to 40_ that connected primarily using _2G_ connection.  


Look at the dataframe above: note that for Minato-ki, New Yorn and Mexico City, the value of the column __"both_18-40_2G"__ is *1000*. The value of '**_1000_**' is retrieved when the Facebook audience that matches our criteria is *equal to or smaller than 1000*. Unfortunately, we cannot tell if the 1000s are really 1000s or something else, like 100s or 0s.

While the default solution is not trusting on values of **1000**, another is trying to finding a more precise estimate. While this is a challenge to do and currently not automatically supported by pySocialWatcher (i.e., no function does it automatically yet), one workaround is submitting API calls that combine multiple criteria and checking the results. For example, for New York, we have 5000 users matching the criteria of __both_18-40_3G__, and if we issued additional API calls for people using either 2G or 3G we might be able to create a column __both_18-40_2G3G__, with let's say 5400 users, meaning that the 1000 for __"both_18-40_2G"__ should actually be something like 400.


Finally, we can save the output file as another csv file [to plot some maps](content:plotting_maps).

In [18]:
final_df.to_csv("processed_top5_cities.csv", index=False)